<a href="https://colab.research.google.com/github/dzikraridha/movie-poster-emotion/blob/main/organise_data.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import numpy as np
import io
import sys
import os.path
import urllib.request
from tqdm import tqdm
from os import listdir
from PIL import Image
import glob

pd.set_option('display.max_colwidth',  None) # Changed -1 to None for unlimited column width
np.set_printoptions(threshold=sys.maxsize)

In [ ]:
df = pd.read_csv("MovieGenre.csv", encoding='ISO-8859-1')
df.head()

imdbId                           Imdb Link  \
0  114709  http://www.imdb.com/title/tt114709   
1  113497  http://www.imdb.com/title/tt113497   
2  113228  http://www.imdb.com/title/tt113228   
3  114885  http://www.imdb.com/title/tt114885   
4  113041  http://www.imdb.com/title/tt113041   

                                Title  IMDB Score                       Genre  \
0                    Toy Story (1995)         8.3  Animation|Adventure|Comedy   
1                      Jumanji (1995)         6.9     Action|Adventure|Family   
2             Grumpier Old Men (1995)         6.6              Comedy|Romance   
3            Waiting to Exhale (1995)         5.7        Comedy|Drama|Romance   
4  Father of the Bride Part II (1995)         5.9       Comedy|Family|Romance   

                                                                                                                                                               Poster  
0   https://images-na.ssl-images-amazon.com/images/M/MV5BMDU2ZWJlMjktMTRhMy00ZTA5LWEzNDgtYmNmZTEwZTViZWJkXkEyXkFqcGdeQXVyNDQ2OTk4MzI@._V1_UX182_CR0,0,182,268_AL_.jpg  
1  https://images-na.ssl-images-amazon.com/images/M/MV5BZTk2ZmUwYmEtNTcwZS00YmMyLWFkYjMtNTRmZDA3YWExMjc2XkEyXkFqcGdeQXVyMTQxNzMzNDI@._V1_UY268_CR10,0,182,268_AL_.jpg  
2   https://images-na.ssl-images-amazon.com/images/M/MV5BMjQxM2YyNjMtZjUxYy00OGYyLTg0MmQtNGE2YzNjYmUyZTY1XkEyXkFqcGdeQXVyMTQxNzMzNDI@._V1_UX182_CR0,0,182,268_AL_.jpg  
3                                   https://images-na.ssl-images-amazon.com/images/M/MV5BMTczMTMyMTgyM15BMl5BanBnXkFtZTcwOTc4OTQyMQ@@._V1_UY268_CR4,0,182,268_AL_.jpg  
4   https://images-na.ssl-images-amazon.com/images/M/MV5BOTEyNzg5NjYtNDU4OS00MWYxLWJhMTItYWU4NTkyNDBmM2Y0XkEyXkFqcGdeQXVyMTQxNzMzNDI@._V1_UX182_CR0,0,182,268_AL_.jpg

In [ ]:
# Drop the 'IMDB Score' and 'Imdb Link' column
df = df.drop('IMDB Score', axis=1)

df = df.drop('Imdb Link', axis=1)

df.head()  # View the first few rows of the dataset

imdbId                               Title                       Genre  \
0  114709                    Toy Story (1995)  Animation|Adventure|Comedy   
1  113497                      Jumanji (1995)     Action|Adventure|Family   
2  113228             Grumpier Old Men (1995)              Comedy|Romance   
3  114885            Waiting to Exhale (1995)        Comedy|Drama|Romance   
4  113041  Father of the Bride Part II (1995)       Comedy|Family|Romance   

                                                                                                                                                               Poster  
0   https://images-na.ssl-images-amazon.com/images/M/MV5BMDU2ZWJlMjktMTRhMy00ZTA5LWEzNDgtYmNmZTEwZTViZWJkXkEyXkFqcGdeQXVyNDQ2OTk4MzI@._V1_UX182_CR0,0,182,268_AL_.jpg  
1  https://images-na.ssl-images-amazon.com/images/M/MV5BZTk2ZmUwYmEtNTcwZS00YmMyLWFkYjMtNTRmZDA3YWExMjc2XkEyXkFqcGdeQXVyMTQxNzMzNDI@._V1_UY268_CR10,0,182,268_AL_.jpg  
2   https://images-na.ssl-images-amazon.com/images/M/MV5BMjQxM2YyNjMtZjUxYy00OGYyLTg0MmQtNGE2YzNjYmUyZTY1XkEyXkFqcGdeQXVyMTQxNzMzNDI@._V1_UX182_CR0,0,182,268_AL_.jpg  
3                                   https://images-na.ssl-images-amazon.com/images/M/MV5BMTczMTMyMTgyM15BMl5BanBnXkFtZTcwOTc4OTQyMQ@@._V1_UY268_CR4,0,182,268_AL_.jpg  
4   https://images-na.ssl-images-amazon.com/images/M/MV5BOTEyNzg5NjYtNDU4OS00MWYxLWJhMTItYWU4NTkyNDBmM2Y0XkEyXkFqcGdeQXVyMTQxNzMzNDI@._V1_UX182_CR0,0,182,268_AL_.jpg

In [ ]:
df.shape

(40108, 4)

In [ ]:
check_nan_in_df = df.isnull().values.any()
print (check_nan_in_df)

True


In [ ]:
#Remove NaN valued entries
df= df.dropna(how='any')
df.shape

(39263, 4)

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import os

# Define the Google Drive path
posters_dir = "/content/drive/My Drive/Posters/"

# Check if the directory exists, create it if it doesn't
if not os.path.exists(posters_dir):
    os.makedirs(posters_dir)


In [ ]:
import urllib.request
import os
from tqdm import tqdm

for index, row in tqdm(df.iterrows()):
    url = row['Poster']
    imdb_id = row['imdbId']

    file_path = os.path.join(posters_dir, f"{imdb_id}.jpg")  # Use os.path.join for better path handling

    try:
        response = urllib.request.urlopen(url)
        if response.getcode() == 200:
            data = response.read()
            with open(file_path, 'wb') as file:
                file.write(data)
            print(f"Successfully downloaded: {imdb_id}")  # Print success message
    except Exception:
        continue  # Simply continue to the next image on error

# No summary of errors or not found images

2it [00:00,  6.27it/s]

Successfully downloaded: 114709
Successfully downloaded: 113497


5it [00:00,  6.98it/s]

Successfully downloaded: 114885
Successfully downloaded: 113041


7it [00:01,  8.15it/s]

...

Successfully downloaded: 83291


39262it [1:34:01,  6.20it/s]

Successfully downloaded: 82875
Successfully downloaded: 815258


39263it [1:34:01,  6.96it/s]

Successfully downloaded: 79142


In [ ]:
# How many images actually downloaded

image_list = []
for file in glob.glob("/content/drive/MyDrive/Posters/*.jpg"):
    image_list.append(file)

print("Number of files found:", len(image_list))

Number of files found: 33944


In [ ]:
# Remove from dataframe those whose posters were not found
df_2 = df[~df['imdbId'].isin(not_found)]
df_2.shape

(39007, 4)

In [ ]:
df_2.head()

imdbId                               Title                       Genre  \
0  114709                    Toy Story (1995)  Animation|Adventure|Comedy   
1  113497                      Jumanji (1995)     Action|Adventure|Family   
3  114885            Waiting to Exhale (1995)        Comedy|Drama|Romance   
4  113041  Father of the Bride Part II (1995)       Comedy|Family|Romance   
5  113277                         Heat (1995)          Action|Crime|Drama   

                                                                                                                                                               Poster  
0   https://images-na.ssl-images-amazon.com/images/M/MV5BMDU2ZWJlMjktMTRhMy00ZTA5LWEzNDgtYmNmZTEwZTViZWJkXkEyXkFqcGdeQXVyNDQ2OTk4MzI@._V1_UX182_CR0,0,182,268_AL_.jpg  
1  https://images-na.ssl-images-amazon.com/images/M/MV5BZTk2ZmUwYmEtNTcwZS00YmMyLWFkYjMtNTRmZDA3YWExMjc2XkEyXkFqcGdeQXVyMTQxNzMzNDI@._V1_UY268_CR10,0,182,268_AL_.jpg  
3                                   https://images-na.ssl-images-amazon.com/images/M/MV5BMTczMTMyMTgyM15BMl5BanBnXkFtZTcwOTc4OTQyMQ@@._V1_UY268_CR4,0,182,268_AL_.jpg  
4   https://images-na.ssl-images-amazon.com/images/M/MV5BOTEyNzg5NjYtNDU4OS00MWYxLWJhMTItYWU4NTkyNDBmM2Y0XkEyXkFqcGdeQXVyMTQxNzMzNDI@._V1_UX182_CR0,0,182,268_AL_.jpg  
5   https://images-na.ssl-images-amazon.com/images/M/MV5BNGMwNzUwNjYtZWM5NS00YzMyLWI4NjAtNjM0ZDBiMzE1YWExXkEyXkFqcGdeQXVyNDk3NzU2MTQ@._V1_UX182_CR0,0,182,268_AL_.jpg

In [ ]:
# Keep only IMDB_ID, Genres, Title

df_3 = df_2[['imdbId','Title','Genre']]
print(df_3.shape)
df_3.head()

(39007, 3)


imdbId                               Title                       Genre
0  114709                    Toy Story (1995)  Animation|Adventure|Comedy
1  113497                      Jumanji (1995)     Action|Adventure|Family
3  114885            Waiting to Exhale (1995)        Comedy|Drama|Romance
4  113041  Father of the Bride Part II (1995)       Comedy|Family|Romance
5  113277                         Heat (1995)          Action|Crime|Drama

In [ ]:
# Resolve mis-match
# Create new dataframe with paths of found images and fill with corresponding metadata from dataframe.

image_paths = []
imdb_id = []
genres = []
titles = []

for file in glob.glob("/content/drive/MyDrive/Posters/*.jpg"):

    base_name = os.path.basename(file)
    img_id, _ = os.path.splitext(base_name)
    #img_id = file.split('.')[0]
    #img_id = file[file.find('/')+1 : file.find('.')]
    title = df_3[df_3["imdbId"] == int(img_id)]["Title"].values[0]
    genre = df_3[df_3["imdbId"] == int(img_id)]["Genre"].values[0]

    image_paths.append(file)
    imdb_id.append(img_id)
    genres.append(genre)
    titles.append(title)


df_4 = pd.DataFrame({'imdbId': imdb_id, 'Genre': genres, 'Title': titles, 'Image_Paths': image_paths})

In [ ]:
print(df_4.shape)
df_4.head()

(33944, 4)


imdbId                       Genre                               Title  \
0  114709  Animation|Adventure|Comedy                    Toy Story (1995)   
1  113497     Action|Adventure|Family                      Jumanji (1995)   
2  114885        Comedy|Drama|Romance            Waiting to Exhale (1995)   
3  113041       Comedy|Family|Romance  Father of the Bride Part II (1995)   
4  113277          Action|Crime|Drama                         Heat (1995)   

                                 Image_Paths  
0  /content/drive/MyDrive/Posters/114709.jpg  
1  /content/drive/MyDrive/Posters/113497.jpg  
2  /content/drive/MyDrive/Posters/114885.jpg  
3  /content/drive/MyDrive/Posters/113041.jpg  
4  /content/drive/MyDrive/Posters/113277.jpg

In [ ]:
# Check which downloaded images are corrupt and remove them
bad_images = []
for file in glob.glob("/content/drive/MyDrive/Posters/*.jpg"):

    try:
        img = Image.open(file) # open image file
        img.verify() # verify its an image
    except (IOError, SyntaxError) as e:
        print('Bad file:', file)

        bad_images.append(file)

print("Number of corrupt files:", len(bad_images))

Number of corrupt files: 0


In [ ]:
# Define the emotion mapping based on genres
emotion_mapping = {
    'Action': ['Surprised', 'Fear', 'Angry'],
    'Adventure': ['Surprised', 'Happy'],
    'Animation': ['Happy', 'Surprised', 'Sad'],
    'Biography': ['Sad', 'Angry', 'Neutral'],
    'Comedy': ['Happy', 'Surprised'],
    'Crime': ['Angry', 'Fear', 'Disgust'],
    'Documentary': ['Neutral','Angry', 'Disgust'],
    'Drama': ['Sad', 'Angry'],
    'Family': ['Happy', 'Sad', 'Neutral'],
    'Fantasy': ['Surprised', 'Happy', 'Fear'],
    'History': ['Sad', 'Angry'],
    'Horror': ['Fear', 'Disgust'],
    'Music': ['Happy', 'Neutral'],
    'Mystery': ['Surprised', 'Fear'],
    'Romance': ['Happy', 'Sad'],
    'Sci-Fi': ['Surprised', 'Fear', 'Disgust'],
    'Sport': ['Happy', 'Surprised'],
    'Thriller': ['Fear', 'Surprised'],
    'War': ['Sad', 'Angry']
}

# Function to map multiple genres to emotions
def map_emotion(genres):
    # Split the genres by delimiter (assuming they are separated by '|')
    genre_list = genres.split('|') if pd.notnull(genres) else []

    # Initialize an empty set to collect emotions
    emotions = set()

    # Loop through the genres and collect emotions
    for genre in genre_list:
        if genre in emotion_mapping:
            emotions.update(emotion_mapping[genre])

    # Return the list of unique emotions (as a sorted list for consistency)
    return list(emotions) if emotions else ['Neutral']

# Apply the function to create a new column 'emotion'
df_4['emotion'] = df_4['Genre'].apply(map_emotion)

# Display the updated dataset
df_4.head()


imdbId                       Genre                               Title  \
0  114709  Animation|Adventure|Comedy                    Toy Story (1995)   
1  113497     Action|Adventure|Family                      Jumanji (1995)   
2  114885        Comedy|Drama|Romance            Waiting to Exhale (1995)   
3  113041       Comedy|Family|Romance  Father of the Bride Part II (1995)   
4  113277          Action|Crime|Drama                         Heat (1995)   

                                 Image_Paths  \
0  /content/drive/MyDrive/Posters/114709.jpg   
1  /content/drive/MyDrive/Posters/113497.jpg   
2  /content/drive/MyDrive/Posters/114885.jpg   
3  /content/drive/MyDrive/Posters/113041.jpg   
4  /content/drive/MyDrive/Posters/113277.jpg   

                                         emotion  
0                        [Happy, Surprised, Sad]  
1  [Fear, Sad, Angry, Neutral, Happy, Surprised]  
2                 [Happy, Angry, Surprised, Sad]  
3               [Happy, Neutral, Surprised, Sad]  
4         [Fear, Sad, Disgust, Angry, Surprised]

In [ ]:
df_4.to_csv("MovieGenreEmotion_clean.csv", index=False)
from google.colab import files
files.download("MovieGenreEmotion_clean.csv")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>